# Klein Bottle (Pseudo 3D)

See original [here](https://nbviewer.org/github/denisvstepanov/lets-plot-examples/blob/master/Klein%20bottle%20-%20pseudo%203D.ipynb).

In [1]:
%useLatestDescriptors
%use lets-plot

In [2]:
import kotlin.math.*

In [3]:
fun linspace(start: Double, end: Double, size: Int): List<Double> {
    return List(size) { i -> start + i * (end - start) / (size - 1) }
}

fun meshgrid(x: List<Double>, y: List<Double>): Pair<List<List<Double>>, List<List<Double>>> {
    return Pair(
        List(y.size) { x.toList() },
        List(y.size) { i -> List(x.size) { y[i] } }
    )
}

fun stackColumns(vararg arrays: List<Double>): List<List<Double>> {
    return List(arrays.first().size) { i -> arrays.map { it[i] } }
}

fun dot(a: List<List<Double>>, b: List<List<Double>>): List<List<Double>> {
    return List(a.size) { i ->
        List(b.first().size) { j ->
            a.first().indices.sumOf { k ->
                a[i][k] * b[k][j]
            }
        }
    }
}

In [4]:
fun bottle(t: List<Double>, p: List<Double>): Triple<List<Double>, List<Double>, List<Double>> {
    val indices = t.indices
    return Triple(
        indices.map { i ->
            -2.0 / 15.0 * cos(t[i]) * (
                3.0 * cos(p[i]) -
                30.0 * sin(t[i]) +
                90.0 * cos(t[i]).pow(4) * sin(t[i]) -
                60.0 * cos(t[i]).pow(6) * sin(t[i]) +
                5.0 * cos(t[i]) * cos(p[i]) * sin(t[i])
            )
        },
        indices.map { i ->
            -1.0 / 15.0 * sin(t[i]) * (
                3.0 * cos(p[i]) -
                3.0 * cos(t[i]).pow(2) * cos(p[i]) -
                48.0 * cos(t[i]).pow(4) * cos(p[i]) +
                48.0 * cos(t[i]).pow(6) * cos(p[i]) -
                60.0 * sin(t[i]) +
                5.0 * cos(t[i]) * cos(p[i]) * sin(t[i]) -
                5.0 * cos(t[i]).pow(3) * cos(p[i]) * sin(t[i]) -
                80.0 * cos(t[i]).pow(5) * cos(p[i]) * sin(t[i]) +
                80.0 * cos(t[i]).pow(7) * cos(p[i]) * sin(t[i])
            )
        },
        indices.map { i ->
            2.0 / 15.0 * (3.0 + 5.0 * cos(t[i]) * sin(t[i])) * sin(p[i])
        }
    )
}

fun rotationMatrices(thetaX: Double, thetaY: Double, thetaZ: Double): Triple<List<List<Double>>, List<List<Double>>, List<List<Double>>> {
    val rX = listOf(
        listOf(1.0, 0.0, 0.0),
        listOf(0.0, cos(thetaX), -sin(thetaX)),
        listOf(0.0, sin(thetaX), cos(thetaX))
    )
    val rY = listOf(
        listOf(cos(thetaY), 0.0, sin(thetaY)),
        listOf(0.0, 1.0, 0.0),
        listOf(-sin(thetaY), 0.0, cos(thetaY)),
    )
    val rZ = listOf(
        listOf(cos(thetaZ), -sin(thetaZ), 0.0),
        listOf(sin(thetaZ), cos(thetaZ), 0.0),
        listOf(0.0, 0.0, 1.0),
    )
    return Triple(rX, rY, rZ)
}

In [5]:
fun getBottleData(n: Int): Map<String, List<Any>> {
    val thetaRange = linspace(0.0, PI, n)
    val phiRange = linspace(0.0, 2 * PI, n)
    val (thetaGrid, phiGrid) = meshgrid(thetaRange, phiRange)
    val theta = thetaGrid.flatten()
    val phi = phiGrid.flatten()
    
    val (x, y, z) = bottle(theta, phi)
    val X = stackColumns(x, y, z)
    
    val (rX, rY, rZ) = rotationMatrices(PI / 6.0, PI / 6.0, PI / 6.0)
    val xRotated = dot(dot(dot(X, rX), rY), rZ)
    
    return mapOf(
        "x" to xRotated.map { it[0] },
        "y" to xRotated.map { it[1] },
        "z" to xRotated.map { it[2] },
        "cross-sectional" to List(n * n) { i -> i % n },
        "longitudinal" to List(n * n) { i -> i / n }
    )
}

In [6]:
val bottleData = getBottleData(100)

In [7]:
val p = ggplot(bottleData) +
    themeVoid() +
    geomPath(alpha = 0.5, color = "gray", sampling = samplingNone) { x = "x"; y = "y"; group = "longitudinal" }
p

In [8]:
p + geomPath(alpha = 0.5, color = "gray", sampling = samplingNone) { x = "x"; y = "y"; group = "cross-sectional" }